In [ ]:
!nvidia-smi

Wed Jun  5 08:09:30 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   39C    P8              10W /  70W |      0MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [ ]:
pip install -q lightning gdown torchmetrics einops torchinfo lpips --no-cache --upgrade

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 13.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 868.8/868.8 kB 24.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.2/43.2 kB 230.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.8/53.8 kB 248.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 802.3/802.3 kB 31.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 158.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 316.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 253.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 251.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 310.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 273.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 284.7 MB/s eta 0:00:00
     ━━━━

In [ ]:
%pip install -q -e git+https://github.com/Kinyugo/consistency_models.git#egg=consistency_models

  Preparing metadata (setup.py) ... done


In [ ]:
import os
os.kill(os.getpid(), 9)

In [ ]:
import json
import os
from dataclasses import asdict, dataclass
from typing import Any, Callable, List, Optional, Tuple, Union

import torch
from einops import rearrange
from einops.layers.torch import Rearrange
from lightning import LightningDataModule, LightningModule, Trainer, seed_everything
from lightning.pytorch.callbacks import LearningRateMonitor
from lightning.pytorch.loggers import TensorBoardLogger
from matplotlib import pyplot as plt
from torch import Tensor, nn
from torch.nn import functional as F
from torch.utils.data import DataLoader
from torchinfo import summary
from torchvision import transforms as T
from torchvision.datasets import ImageFolder
from torchvision.utils import make_grid

from consistency_models import (
    ConsistencySamplingAndEditing,
    ImprovedConsistencyTraining,
    pseudo_huber_loss,
)
from consistency_models.utils import update_ema_model_

In [ ]:
torch.__version__

'2.3.0+cu121'

In [ ]:
import sys
sys.version

'3.10.12 (main, Nov 20 2023, 15:14:05) [GCC 11.4.0]'

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
%cd /content/drive/MyDrive/

In [ ]:
!cp train_z.npy /content

In [ ]:
%cd /content

/content


In [ ]:
import numpy as np
import torch
from torch.utils.data import DataLoader, Dataset
from typing import Tuple, Optional
from dataclasses import dataclass

@dataclass
class TabularDataModuleConfig:
    data_dir: str = "train_z.npy"
    z_size: Tuple[int, int] = (85, 4)
    batch_size: int = 256
    num_workers: int = 8
    pin_memory: bool = True
    persistent_workers: bool = True


class TabularDataModule(LightningDataModule):
    def __init__(self, config: TabularDataModuleConfig) -> None:
        super().__init__()
        self.config = config

    def setup(self, stage: Optional[str] = None) -> None:

        # Assuming the entire data is used for a single purpose, e.g., training
        self.dataset = torch.Tensor(np.load(config.data_dir))
        self.dataset = self.dataset.reshape(self.dataset.shape[0], -1)

    def train_dataloader(self) -> DataLoader:
        return DataLoader(
            self.dataset,
            batch_size=self.config.batch_size,
            shuffle=True,
            num_workers=self.config.num_workers,
            pin_memory=self.config.pin_memory,
            persistent_workers=self.config.persistent_workers,
        )

# Example usage
# Assume numpy_data is your loaded numpy array of table data
config = TabularDataModuleConfig()


In [ ]:
@dataclass
class MLPDiffusionConfig:
    d_in: int = 85 * 4
    noise_level_channels: int = 2048
    noise_level_scale: float = 0.02


class MLPDiffusion(nn.Module):
    def __init__(self, config: MLPDiffusionConfig):
        super().__init__()

        d_in = config.d_in
        dim_t = config.noise_level_channels

        self.config = config
        self.proj = nn.Linear(d_in, dim_t)


        self.mlp = nn.Sequential(
            nn.Linear(dim_t, dim_t * 2),
            nn.SiLU(),
            nn.Linear(dim_t * 2, dim_t * 2),
            nn.SiLU(),
            nn.Linear(dim_t * 2, dim_t),
            nn.SiLU(),
            nn.Linear(dim_t, d_in),
        )

        '''self.map_noise = PositionalEmbedding(num_channels=dim_t)
        self.time_embed = nn.Sequential(
            nn.Linear(dim_t, dim_t),
            nn.SiLU(),
            nn.Linear(dim_t, dim_t)
        )'''

        self.noise_level_embedding = NoiseLevelEmbedding(
            config.noise_level_channels, config.noise_level_scale
        )

    def forward(self, x, noise_level):
        noise_level = self.noise_level_embedding(noise_level)

        #emb = self.map_noise(noise_labels)
        #emb = emb.reshape(emb.shape[0], 2, -1).flip(1).reshape(*emb.shape) # swap sin/cos
        #emb = self.time_embed(emb)


        #print('-----------------------')
        #print(x.shape)
        #print('-----------------------')
        #print(noise_level.shape)

        x = self.proj(x) + noise_level
        return self.mlp(x)

    def save_pretrained(self, pretrained_path: str) -> None:
        os.makedirs(pretrained_path, exist_ok=True)

        with open(os.path.join(pretrained_path, "config.json"), mode="w") as f:
            json.dump(asdict(self.config), f)

        torch.save(self.state_dict(), os.path.join(pretrained_path, "model.pt"))

    @classmethod
    def from_pretrained(cls, pretrained_path: str) -> "MLPDiffusion":
        with open(os.path.join(pretrained_path, "config.json"), mode="r") as f:
            config_dict = json.load(f)
        config = MLPDiffusionConfig(**config_dict)

        model = cls(config)

        state_dict = torch.load(
            os.path.join(pretrained_path, "model.pt"), map_location=torch.device("cpu")
        )
        model.load_state_dict(state_dict)

        return model



class NoiseLevelEmbedding(nn.Module):
    def __init__(self, channels: int, scale: float = 0.02) -> None:
        super().__init__()

        self.W = nn.Parameter(torch.randn(channels // 2) * scale, requires_grad=False)

        self.projection = nn.Sequential(
            nn.Linear(channels, 4 * channels),
            nn.SiLU(),
            nn.Linear(4 * channels, channels),
            #Rearrange("b c -> b c () ()"),
        )

    def forward(self, x: Tensor) -> Tensor:
        h = x[:, None] * self.W[None, :] * 2 * torch.pi
        h = torch.cat([torch.sin(h), torch.cos(h)], dim=-1)

        return self.projection(h)

In [ ]:
@dataclass
class LitImprovedConsistencyModelConfig:
    ema_decay_rate: float = 0.99993
    lr: float = 1e-4
    betas: Tuple[float, float] = (0.9, 0.995)
    lr_scheduler_start_factor: float = 1e-5
    lr_scheduler_iters: int = 10_000
    sample_every_n_steps: int = 10_000
    num_samples: int = 8
    sampling_sigmas: Tuple[Tuple[int, ...], ...] = (
        (80,),
        (80.0, 0.661),
        (80.0, 24.4, 5.84, 0.9, 0.661),
    )


class LitImprovedConsistencyModel(LightningModule):
    def __init__(
        self,
        consistency_training: ImprovedConsistencyTraining,
        consistency_sampling: ConsistencySamplingAndEditing,
        model: MLPDiffusion,
        ema_model: MLPDiffusion,
        config: LitImprovedConsistencyModelConfig,
    ) -> None:
        super().__init__()

        self.consistency_training = consistency_training
        self.consistency_sampling = consistency_sampling
        self.model = model
        self.ema_model = ema_model
        self.config = config

        # Freeze the EMA model and set it to eval mode
        for param in self.ema_model.parameters():
            param.requires_grad = False
        self.ema_model = self.ema_model.eval()

    def training_step(self, batch: Union[Tensor, List[Tensor]], batch_idx: int) -> None:
        if isinstance(batch, list):
            batch = batch[0]

        output = self.consistency_training(
            self.model, batch, self.global_step, self.trainer.max_steps
        )

        loss = (
            pseudo_huber_loss(output.predicted, output.target) * output.loss_weights
        ).mean()

        self.log_dict({"train_loss": loss, "num_timesteps": output.num_timesteps})

        return loss

    def on_train_batch_end(
        self, outputs: Any, batch: Union[Tensor, List[Tensor]], batch_idx: int
    ) -> None:
        update_ema_model_(self.model, self.ema_model, self.config.ema_decay_rate)

        if (
            (self.global_step + 1) % self.config.sample_every_n_steps == 0
        ) or self.global_step == 0:
            self.__sample_and_log_samples(batch)

    def configure_optimizers(self):
        opt = torch.optim.Adam(
            self.model.parameters(), lr=self.config.lr, betas=self.config.betas
        )
        sched = torch.optim.lr_scheduler.LinearLR(
            opt,
            start_factor=self.config.lr_scheduler_start_factor,
            total_iters=self.config.lr_scheduler_iters,
        )
        sched = {"scheduler": sched, "interval": "step", "frequency": 1}

        return [opt], [sched]

    @torch.no_grad()
    def __sample_and_log_samples(self, batch: Union[Tensor, List[Tensor]]) -> None:
        if isinstance(batch, list):
            batch = batch[0]

        # Ensure the number of samples does not exceed the batch size
        num_samples = min(self.config.num_samples, batch.shape[0])
        noise = torch.randn_like(batch[:num_samples])

        # Log ground truth samples
        self.__log_images(
            batch[:num_samples].detach().clone(), f"ground_truth", self.global_step
        )

        for sigmas in self.config.sampling_sigmas:
            samples = self.consistency_sampling(
                self.ema_model, noise, sigmas, clip_denoised=True, verbose=True
            )
            samples = samples.clamp(min=-1.0, max=1.0)

            # Generated samples
            self.__log_images(
                samples,
                f"generated_samples-sigmas={sigmas}",
                self.global_step,
            )

    @torch.no_grad()
    def __log_images(self, images: Tensor, title: str, global_step: int) -> None:
        images = images.detach().float()

        grid = make_grid(
            images.clamp(-1.0, 1.0), value_range=(-1.0, 1.0), normalize=True
        )
        self.logger.experiment.add_image(title, grid, global_step)

In [ ]:
@dataclass
class TrainingConfig:
    image_dm_config: TabularDataModuleConfig
    unet_config: MLPDiffusionConfig
    consistency_training: ImprovedConsistencyTraining
    consistency_sampling: ConsistencySamplingAndEditing
    lit_icm_config: LitImprovedConsistencyModelConfig
    trainer: Trainer
    seed: int = 42
    model_ckpt_path: str = "checkpoints/icm"
    resume_ckpt_path: Optional[str] = None


def run_training(config: TrainingConfig) -> None:
    # Set seed
    seed_everything(config.seed)

    # Create data module
    dm = TabularDataModule(config.image_dm_config)

    # Create model and its EMA
    model = MLPDiffusion(config.unet_config)
    ema_model = MLPDiffusion(config.unet_config)
    ema_model.load_state_dict(model.state_dict())

    # Create lightning module
    lit_icm = LitImprovedConsistencyModel(
        config.consistency_training,
        config.consistency_sampling,
        model,
        ema_model,
        config.lit_icm_config,
    )

    # Run training
    config.trainer.fit(lit_icm, dm, ckpt_path=config.resume_ckpt_path)

    # Save model
    lit_icm.model.save_pretrained(config.model_ckpt_path)

In [ ]:
training_config = TrainingConfig(
    image_dm_config=TabularDataModuleConfig(),
    unet_config=MLPDiffusionConfig(),
    consistency_training=ImprovedConsistencyTraining(final_timesteps=11),
    consistency_sampling=ConsistencySamplingAndEditing(),
    lit_icm_config=LitImprovedConsistencyModelConfig(
        sample_every_n_steps=1000, lr_scheduler_iters=1000
    ),
    trainer=Trainer(
        max_steps=100_000,
        precision="16-mixed",
        log_every_n_steps=10,
        logger=TensorBoardLogger(".", name="logs", version="icm"),
        callbacks=[LearningRateMonitor(logging_interval="step")],
    ),
)
run_training(training_config)

INFO: Using 16bit Automatic Mixed Precision (AMP)
INFO:lightning.pytorch.utilities.rank_zero:Using 16bit Automatic Mixed Precision (AMP)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: IPU available: False, using: 0 IPUs
INFO:lightning.pytorch.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: Seed set to 42
INFO:lightning.fabric.utilities.seed:Seed set to 42
/usr/local/lib/python3.10/dist-packages/lightning/pytorch/callbacks/model_checkpoint.py:653: Checkpoint directory ./logs/icm/checkpoints exists and is not empty.
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [

Training: |          | 0/? [00:00<?, ?it/s]

0it [00:00, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

...

  0%|          | 0/4 [00:00<?, ?it/s]

0it [00:00, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

INFO: `Trainer.fit` stopped: `max_steps=100000` reached.
INFO:lightning.pytorch.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=100000` reached.


In [ ]:
!zip -r checkpoints.zip /content/checkpoints/

  adding: content/checkpoints/ (stored 0%)
  adding: content/checkpoints/icm/ (stored 0%)
  adding: content/checkpoints/icm/model.pt (deflated 8%)
  adding: content/checkpoints/icm/config.json (deflated 20%)


In [ ]:
!zip -r logs.zip /content/logs/

  adding: content/logs/ (stored 0%)
  adding: content/logs/icm/ (stored 0%)
  adding: content/logs/icm/events.out.tfevents.1717576949.06edef013a67.12057.0 (deflated 33%)
  adding: content/logs/icm/hparams.yaml (stored 0%)
  adding: content/logs/icm/events.out.tfevents.1717576815.06edef013a67.3792.1 (deflated 34%)
  adding: content/logs/icm/checkpoints/ (stored 0%)
  adding: content/logs/icm/checkpoints/epoch=4-step=10470.ckpt (deflated 8%)
  adding: content/logs/icm/checkpoints/epoch=47-step=100000.ckpt (deflated 8%)
  adding: content/logs/icm/checkpoints/epoch=0-step=2094.ckpt (deflated 9%)
  adding: content/logs/icm/events.out.tfevents.1717577452.06edef013a67.14462.0 (deflated 34%)


In [ ]:
!cp checkpoints.zip /content/drive/MyDrive/

In [ ]:
!cp logs.zip /content/drive/MyDrive/

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
seed_everything(42)

INFO: Seed set to 42
INFO:lightning.fabric.utilities.seed:Seed set to 42


42

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
dtype = torch.bfloat16 if torch.cuda.is_available() else torch.float32

unet = MLPDiffusion.from_pretrained("checkpoints/icm").eval().to(device=device, dtype=dtype)

In [ ]:
consistency_sampling_and_editing = ConsistencySamplingAndEditing()
batch_size = 50000

start_time = time.time()
with torch.no_grad():
    samples = consistency_sampling_and_editing(
        unet,
        torch.randn((50000, 340), device=device, dtype=dtype),
        #start_from_y = False,
        sigmas=[80.0, 24.4, 5.84, 0.9, 0.661],  # Use more steps for better samples e.g 2-5
        #clip_denoised=True,
        verbose=True,
    )
    samples = samples.view(50000, 85, 4)
end_time = time.time()
print(f"Total time taken: {end_time - start_time} seconds")

  0%|          | 0/4 [00:00<?, ?it/s]

Total time taken: 0.024181842803955078 seconds


  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

...

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

Total time taken: 109.36147499084473 seconds


In [ ]:
import torch
import time

total_samples = 535926
batch_size = 50000

# 计算需要多少个完整批次，以及最后一个批次的大小
num_full_batches = total_samples // batch_size
last_batch_size = total_samples % batch_size

all_samples = torch.empty((total_samples, 85, 4), device=device, dtype=dtype)

start_time = time.time()

with torch.no_grad():
    for i in range(num_full_batches + (1 if last_batch_size > 0 else 0)):
        current_batch_size = batch_size if i < num_full_batches else last_batch_size
        samples = consistency_sampling_and_editing(
            unet,
            torch.randn((current_batch_size, 340), device=device, dtype=dtype),
            sigmas=[80.0, 24.4],
            verbose=True,
        )
        samples = samples.view(current_batch_size, 85, 4)
        all_samples[i * batch_size: i * batch_size + current_batch_size] = samples

end_time = time.time()
print(f"Total time taken: {end_time - start_time} seconds")

all_samples = all_samples.to(dtype=torch.float32)

all_samples = all_samples.cpu()
all_samples_numpy = all_samples.numpy()
np.save('sample_2step.npy', all_samples_numpy)

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Total time taken: 0.20772051811218262 seconds


In [ ]:
import torch
import time

total_samples = 535926
batch_size = 50000

# 计算需要多少个完整批次，以及最后一个批次的大小
num_full_batches = total_samples // batch_size
last_batch_size = total_samples % batch_size

all_samples = torch.empty((total_samples, 85, 4), device=device, dtype=dtype)

start_time = time.time()

with torch.no_grad():
    for i in range(num_full_batches + (1 if last_batch_size > 0 else 0)):
        current_batch_size = batch_size if i < num_full_batches else last_batch_size
        samples = consistency_sampling_and_editing(
            unet,
            torch.randn((current_batch_size, 340), device=device, dtype=dtype),
            sigmas=[80.0],
            verbose=True,
        )
        samples = samples.view(current_batch_size, 85, 4)
        all_samples[i * batch_size: i * batch_size + current_batch_size] = samples

end_time = time.time()
print(f"Total time taken: {end_time - start_time} seconds")

all_samples = all_samples.to(dtype=torch.float32)

all_samples = all_samples.cpu()
all_samples_numpy = all_samples.numpy()
np.save('sample_1step.npy', all_samples_numpy)

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

...

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

Total time taken: 0.1925497055053711 seconds


In [ ]:
!cp sample_5step.npy /content/drive/MyDrive/

In [ ]:
!cp sample_2step.npy /content/drive/MyDrive/

In [ ]:
!cp sample_1step.npy /content/drive/MyDrive/